## Predicting Mobility through Measures with One-Hot Encoder

#### Importing and adjusting the datasets

In [21]:
# Importing the libraries
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd

In [164]:
# Import the dataset for trade
trade = pd.read_csv("../data/usitc/tradeVariables-mxcan.csv")

In [165]:
trade.head()

year       exports       imports  travel_mx  travel_can
0  1996  5.468587e+10  7.296319e+10  276751448   153038903
1  1997  6.839322e+10  8.587234e+10  348661488   145512710
2  1998  7.536930e+10  9.470867e+10  366296614   142291790
3  1999  8.138074e+10  1.100000e+11  391959396   146497328
4  2000  1.000000e+11  1.360000e+11  392231869   147789673

In [166]:
# Import the dataset for mobility
mobility = pd.read_csv("../data/usitc/border_crossing_entry_data_trade.csv")

In [167]:
mobility.head()

Port Name State  Port Code            Border            Date  \
0         Alexandria Bay    NY        708  US-Canada Border  12/1/2019 0:00   
1               Baudette    MN       3424  US-Canada Border  12/1/2019 0:00   
2                 Blaine    WA       3004  US-Canada Border  12/1/2019 0:00   
3            Brownsville    TX       2301  US-Mexico Border  12/1/2019 0:00   
4  Buffalo-Niagara Falls    NY        901  US-Canada Border  12/1/2019 0:00   

          Measure  Value       imports       exports  
0  Bus Passengers    740           NaN           NaN  
1  Bus Passengers     83           NaN           NaN  
2  Bus Passengers  17029           NaN           NaN  
3  Bus Passengers   4668  3.580000e+11  1.960000e+11  
4  Bus Passengers   9910           NaN           NaN

In [168]:
# Include only mobility on the US-MX border
borderMX = mobility[(mobility['Border']=="US-Mexico Border")]

In [169]:
mxVar = list(borderMX.columns)
print(mxVar)

['Port Name', 'State', 'Port Code', 'Border', 'Date', 'Measure', 'Value', 'imports', 'exports']


In [170]:
# Extract year and consolidate year
import datetime
borderMX['year']= pd.DatetimeIndex(borderMX['Date']).year

C:\Users\nhinojos\AppData\Local\Continuum\anaconda\lib\site-packages\ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  This is separate from the ipykernel package so we can avoid doing imports until


In [171]:
borderMX.head()

Port Name State  Port Code            Border            Date  \
3     Brownsville    TX       2301  US-Mexico Border  12/1/2019 0:00   
6   Calexico East    CA       2507  US-Mexico Border  12/1/2019 0:00   
8        Columbus    NM       2406  US-Mexico Border  12/1/2019 0:00   
11        Douglas    AZ       2601  US-Mexico Border  12/1/2019 0:00   
13     Eagle Pass    TX       2303  US-Mexico Border  12/1/2019 0:00   

           Measure  Value       imports       exports  year  
3   Bus Passengers   4668  3.580000e+11  1.960000e+11  2019  
6   Bus Passengers   4080  3.580000e+11  1.960000e+11  2019  
8   Bus Passengers   1452  3.580000e+11  1.960000e+11  2019  
11  Bus Passengers    107  3.580000e+11  1.960000e+11  2019  
13  Bus Passengers   8525  3.580000e+11  1.960000e+11  2019

## Building data frame for multivariate regression

In [33]:
borderMX["State"].nunique()

4

In [34]:
borderMX["Measure"].nunique()

12

In [174]:
df = borderMX[["year","State","Port Code","Value"]].copy()

In [175]:
df.shape

(82288, 4)

In [177]:
X = df.iloc[:,:-1].values
y = df.iloc[:,3].values

In [223]:
y = df.iloc[:,3].values

In [181]:
print(X.shape)

(82288, 6)


In [111]:
print(y.shape)

(82288,)


## Encoding categorial variables

In [172]:
# Encoding categorical data
# Encoding the independent variable
from sklearn.preprocessing import LabelEncoder, OneHotEncoder

In [178]:
labelencoder = LabelEncoder()
X[:, 1] = labelencoder.fit_transform(X[:, 1])
onehotencoder = OneHotEncoder(categorical_features = [1])
X = onehotencoder.fit_transform(X).toarray()

C:\Users\nhinojos\AppData\Local\Continuum\anaconda\lib\site-packages\sklearn\preprocessing\_encoders.py:368: FutureWarning: The handling of integer data will change in version 0.22. Currently, the categories are determined based on the range [0, max(values)], while in the future they will be determined based on the unique values.
If you want the future behaviour and silence this warning, you can specify "categories='auto'".
In case you used a LabelEncoder before this OneHotEncoder to convert the categories to integers, then you can now use the OneHotEncoder directly.
  warnings.warn(msg, FutureWarning)
C:\Users\nhinojos\AppData\Local\Continuum\anaconda\lib\site-packages\sklearn\preprocessing\_encoders.py:390: DeprecationWarning: The 'categorical_features' keyword is deprecated in version 0.20 and will be removed in 0.22. You can use the ColumnTransformer instead.
  "use the ColumnTransformer instead.", DeprecationWarning)


In [179]:
print(X)

[[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.019e+03 2.301e+03]
 [0.000e+00 1.000e+00 0.000e+00 0.000e+00 2.019e+03 2.507e+03]
 [0.000e+00 0.000e+00 1.000e+00 0.000e+00 2.019e+03 2.406e+03]
 ...
 [0.000e+00 0.000e+00 1.000e+00 0.000e+00 1.996e+03 2.408e+03]
 [0.000e+00 0.000e+00 0.000e+00 1.000e+00 1.996e+03 2.403e+03]
 [0.000e+00 1.000e+00 0.000e+00 0.000e+00 1.996e+03 2.505e+03]]


In [180]:
print(X.shape)

(82288, 6)


In [ ]:
# Avoid the dummy variable trap, but for Python this is taken care of
# X=X[:,1:]

In [79]:
# Splitting the dataset into the Training set and Test set
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.2, random_state = 0)

In [80]:
print(X_train.size)

394980


In [81]:
# No need to take care of feature scaling, the library will take care of it for us

## Fitting Multple LInear Regression to the Training Set

In [82]:
from sklearn.linear_model import LinearRegression

In [83]:
# Call the class LinearRegression() and assign to regressor
# Creating an object of the class LinearRegression
regressor = LinearRegression()

In [84]:
# Fit the object to the training set
# Apply the fit method
regressor.fit(X_train, y_train)

LinearRegression(copy_X=True, fit_intercept=True, n_jobs=None,
         normalize=False)

In [85]:
# No graph necessarily due to dimensions
# Prediction of the test set results
# Predict observations of the test set
y_pred = regressor.predict(X_test)

In [86]:
print(y_pred)

[132169.18711905  93099.99170899 132506.24264267 ... 137741.04632209
  41292.46861524  96333.26593841]


In [87]:
print(y_test)

[523   0   0 ...   0  22   0]


In [89]:
predictions = y_pred
real = y_test

## Start backwards elimination to build a better model

In [126]:
im = borderMX.iloc[:,[7]].values

In [138]:
ex = borderMX.iloc[:,[8]].values

In [139]:
print(ex.shape)

(82288, 1)


In [100]:
import statsmodels.api as sm

In [194]:
print(X.shape)

(82288, 8)


In [192]:
X = np.append(arr=X, values= im.astype(float),axis=1)

In [193]:
X = np.append(arr=X, values= ex.astype(float),axis=1)

In [195]:
print(X)

[[0.00000000e+00 0.00000000e+00 0.00000000e+00 ... 2.30100000e+03
  3.58000000e+11 1.96000000e+11]
 [0.00000000e+00 1.00000000e+00 0.00000000e+00 ... 2.50700000e+03
  3.58000000e+11 1.96000000e+11]
 [0.00000000e+00 0.00000000e+00 1.00000000e+00 ... 2.40600000e+03
  3.58000000e+11 1.96000000e+11]
 ...
 [0.00000000e+00 0.00000000e+00 1.00000000e+00 ... 2.40800000e+03
  7.29631894e+10 5.46858652e+10]
 [0.00000000e+00 0.00000000e+00 0.00000000e+00 ... 2.40300000e+03
  7.29631894e+10 5.46858652e+10]
 [0.00000000e+00 1.00000000e+00 0.00000000e+00 ... 2.50500000e+03
  7.29631894e+10 5.46858652e+10]]


In [158]:
## Added imports and exports
## Adding B0 to the X matrix

X = np.append(arr=np.ones((82288,1)).astype(int),values =X, axis=1)

In [184]:
print(X)

[[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.019e+03 2.301e+03]
 [0.000e+00 1.000e+00 0.000e+00 0.000e+00 2.019e+03 2.507e+03]
 [0.000e+00 0.000e+00 1.000e+00 0.000e+00 2.019e+03 2.406e+03]
 ...
 [0.000e+00 0.000e+00 1.000e+00 0.000e+00 1.996e+03 2.408e+03]
 [0.000e+00 0.000e+00 0.000e+00 1.000e+00 1.996e+03 2.403e+03]
 [0.000e+00 1.000e+00 0.000e+00 0.000e+00 1.996e+03 2.505e+03]]


In [196]:
arr = X
for a in arr:
    print(a)

[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.019e+03 2.301e+03 3.580e+11
 1.960e+11]
[0.000e+00 1.000e+00 0.000e+00 0.000e+00 2.019e+03 2.507e+03 3.580e+11
 1.960e+11]
[0.000e+00 0.000e+00 1.000e+00 0.000e+00 2.019e+03 2.406e+03 3.580e+11
 1.960e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.019e+03 2.601e+03 3.580e+11
 1.960e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.019e+03 2.303e+03 3.580e+11
 1.960e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.019e+03 2.402e+03 3.580e+11
 1.960e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.019e+03 2.305e+03 3.580e+11
 1.960e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.019e+03 2.304e+03 3.580e+11
 1.960e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.019e+03 2.602e+03 3.580e+11
 1.960e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.019e+03 2.604e+03 3.580e+11
 1.960e+11]
[0.000e+00 1.000e+00 0.000e+00 0.000e+00 2.019e+03 2.506e+03 3.580e+11
 1.960e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.019e+03 2.403e+03 3.580e+11
 1.960e+11]
[0.0

 1.960e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.019e+03 2.310e+03 3.580e+11
 1.960e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.019e+03 2.608e+03 3.580e+11
 1.960e+11]
[0.000e+00 0.000e+00 1.000e+00 0.000e+00 2.019e+03 2.408e+03 3.580e+11
 1.960e+11]
[0.000e+00 1.000e+00 0.000e+00 0.000e+00 2.019e+03 2.505e+03 3.580e+11
 1.960e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.019e+03 2.301e+03 3.580e+11
 1.960e+11]
[0.000e+00 1.000e+00 0.000e+00 0.000e+00 2.019e+03 2.507e+03 3.580e+11
 1.960e+11]
[0.000e+00 0.000e+00 1.000e+00 0.000e+00 2.019e+03 2.406e+03 3.580e+11
 1.960e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.019e+03 2.302e+03 3.580e+11
 1.960e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.019e+03 2.601e+03 3.580e+11
 1.960e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.019e+03 2.303e+03 3.580e+11
 1.960e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.019e+03 2.402e+03 3.580e+11
 1.960e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.019e+03 2.305e+03 3.580e+11
 1.9

[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.019e+03 2.310e+03 3.580e+11
 1.960e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.019e+03 2.310e+03 3.580e+11
 1.960e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.019e+03 2.310e+03 3.580e+11
 1.960e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.019e+03 2.310e+03 3.580e+11
 1.960e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.019e+03 2.608e+03 3.580e+11
 1.960e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.019e+03 2.608e+03 3.580e+11
 1.960e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.019e+03 2.608e+03 3.580e+11
 1.960e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.019e+03 2.608e+03 3.580e+11
 1.960e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.019e+03 2.608e+03 3.580e+11
 1.960e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.019e+03 2.608e+03 3.580e+11
 1.960e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.019e+03 2.608e+03 3.580e+11
 1.960e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.019e+03 2.608e+03 3.580e+11
 1.960e+11]
[0.0

 1.960e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.019e+03 2.602e+03 3.580e+11
 1.960e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.019e+03 2.602e+03 3.580e+11
 1.960e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.019e+03 2.602e+03 3.580e+11
 1.960e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.019e+03 2.602e+03 3.580e+11
 1.960e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.019e+03 2.602e+03 3.580e+11
 1.960e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.019e+03 2.602e+03 3.580e+11
 1.960e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.019e+03 2.602e+03 3.580e+11
 1.960e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.019e+03 2.601e+03 3.580e+11
 1.960e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.019e+03 2.601e+03 3.580e+11
 1.960e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.019e+03 2.601e+03 3.580e+11
 1.960e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.019e+03 2.601e+03 3.580e+11
 1.960e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.019e+03 2.601e+03 3.580e+11
 1.9

[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.019e+03 2.309e+03 3.580e+11
 1.960e+11]
[0.000e+00 1.000e+00 0.000e+00 0.000e+00 2.019e+03 2.507e+03 3.580e+11
 1.960e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.019e+03 2.603e+03 3.580e+11
 1.960e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.019e+03 2.601e+03 3.580e+11
 1.960e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.019e+03 2.402e+03 3.580e+11
 1.960e+11]
[0.000e+00 1.000e+00 0.000e+00 0.000e+00 2.019e+03 2.502e+03 3.580e+11
 1.960e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.019e+03 2.604e+03 3.580e+11
 1.960e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.019e+03 2.310e+03 3.580e+11
 1.960e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.019e+03 2.604e+03 3.580e+11
 1.960e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.019e+03 2.307e+03 3.580e+11
 1.960e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.019e+03 2.302e+03 3.580e+11
 1.960e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.019e+03 2.402e+03 3.580e+11
 1.960e+11]
[1.0

...

 1.190e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.007e+03 2.310e+03 2.110e+11
 1.190e+11]
[0.000e+00 1.000e+00 0.000e+00 0.000e+00 2.007e+03 2.504e+03 2.110e+11
 1.190e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.007e+03 2.403e+03 2.110e+11
 1.190e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.007e+03 2.305e+03 2.110e+11
 1.190e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.007e+03 2.601e+03 2.110e+11
 1.190e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.007e+03 2.305e+03 2.110e+11
 1.190e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.007e+03 2.606e+03 2.110e+11
 1.190e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.007e+03 2.603e+03 2.110e+11
 1.190e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.007e+03 2.602e+03 2.110e+11
 1.190e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.007e+03 2.606e+03 2.110e+11
 1.190e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.007e+03 2.403e+03 2.110e+11
 1.190e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.007e+03 2.604e+03 2.110e+11
 1.1

[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.007e+03 2.602e+03 2.110e+11
 1.190e+11]
[0.000e+00 0.000e+00 1.000e+00 0.000e+00 2.007e+03 2.406e+03 2.110e+11
 1.190e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.007e+03 2.603e+03 2.110e+11
 1.190e+11]
[0.000e+00 1.000e+00 0.000e+00 0.000e+00 2.007e+03 2.504e+03 2.110e+11
 1.190e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.007e+03 2.305e+03 2.110e+11
 1.190e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.007e+03 2.608e+03 2.110e+11
 1.190e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.007e+03 2.304e+03 2.110e+11
 1.190e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.007e+03 2.305e+03 2.110e+11
 1.190e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.007e+03 2.402e+03 2.110e+11
 1.190e+11]
[0.000e+00 1.000e+00 0.000e+00 0.000e+00 2.007e+03 2.503e+03 2.110e+11
 1.190e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.007e+03 2.302e+03 2.110e+11
 1.190e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.007e+03 2.310e+03 2.110e+11
 1.190e+11]
[0.0

 1.190e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.007e+03 2.601e+03 2.110e+11
 1.190e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.007e+03 2.310e+03 2.110e+11
 1.190e+11]
[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.007e+03 2.602e+03 2.110e+11
 1.190e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.007e+03 2.402e+03 2.110e+11
 1.190e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.007e+03 2.303e+03 2.110e+11
 1.190e+11]
[0.000e+00 1.000e+00 0.000e+00 0.000e+00 2.007e+03 2.507e+03 2.110e+11
 1.190e+11]
[0.000e+00 1.000e+00 0.000e+00 0.000e+00 2.007e+03 2.505e+03 2.110e+11
 1.190e+11]
[0.000e+00 0.000e+00 1.000e+00 0.000e+00 2.007e+03 2.406e+03 2.110e+11
 1.190e+11]
[0.000e+00 1.000e+00 0.000e+00 0.000e+00 2.007e+03 2.503e+03 2.110e+11
 1.190e+11]
[0.000e+00 1.000e+00 0.000e+00 0.000e+00 2.007e+03 2.502e+03 2.110e+11
 1.190e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.007e+03 2.303e+03 2.110e+11
 1.190e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.007e+03 2.303e+03 2.110e+11
 1.1

[1.000e+00 0.000e+00 0.000e+00 0.000e+00 2.007e+03 2.602e+03 2.110e+11
 1.190e+11]
[0.000e+00 1.000e+00 0.000e+00 0.000e+00 2.007e+03 2.502e+03 2.110e+11
 1.190e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.007e+03 2.404e+03 2.110e+11
 1.190e+11]
[0.000e+00 1.000e+00 0.000e+00 0.000e+00 2.007e+03 2.506e+03 2.110e+11
 1.190e+11]
[0.000e+00 1.000e+00 0.000e+00 0.000e+00 2.007e+03 2.502e+03 2.110e+11
 1.190e+11]
[0.000e+00 1.000e+00 0.000e+00 0.000e+00 2.007e+03 2.506e+03 2.110e+11
 1.190e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.007e+03 2.303e+03 2.110e+11
 1.190e+11]
[0.000e+00 1.000e+00 0.000e+00 0.000e+00 2.007e+03 2.505e+03 2.110e+11
 1.190e+11]
[0.000e+00 1.000e+00 0.000e+00 0.000e+00 2.007e+03 2.507e+03 2.110e+11
 1.190e+11]
[0.000e+00 1.000e+00 0.000e+00 0.000e+00 2.007e+03 2.502e+03 2.110e+11
 1.190e+11]
[0.000e+00 1.000e+00 0.000e+00 0.000e+00 2.007e+03 2.503e+03 2.110e+11
 1.190e+11]
[0.000e+00 0.000e+00 0.000e+00 1.000e+00 2.007e+03 2.304e+03 2.110e+11
 1.190e+11]
[0.0

KeyboardInterrupt: 

In [198]:
print(X.shape)

(82288, 8)


In [199]:
## Adding B0 to the calculations

X = np.append(arr=np.ones((82288,1)).astype(int),values =X, axis=1)

In [200]:
print(X.shape)

(82288, 9)


## SUCCESS! NEW ESTABLISHED MATRIX X HERE 

#### Backwards elimination

In [222]:
# Create a new matrix of features to create new optimal matrix of features
# Including all independent variables
# Choosing a 0.1 significance level
X_opt = X[:,[0,1,2,3,5,6,7,8]]
print(X_opt)


[[1.00000000e+00 0.00000000e+00 0.00000000e+00 ... 2.30100000e+03
  3.58000000e+11 1.96000000e+11]
 [1.00000000e+00 0.00000000e+00 1.00000000e+00 ... 2.50700000e+03
  3.58000000e+11 1.96000000e+11]
 [1.00000000e+00 0.00000000e+00 0.00000000e+00 ... 2.40600000e+03
  3.58000000e+11 1.96000000e+11]
 ...
 [1.00000000e+00 0.00000000e+00 0.00000000e+00 ... 2.40800000e+03
  7.29631894e+10 5.46858652e+10]
 [1.00000000e+00 0.00000000e+00 0.00000000e+00 ... 2.40300000e+03
  7.29631894e+10 5.46858652e+10]
 [1.00000000e+00 0.00000000e+00 1.00000000e+00 ... 2.50500000e+03
  7.29631894e+10 5.46858652e+10]]


In [224]:
# Fitting model with all matrix of features
# Contains all the possible predictors
# Ordinary Least Squares

regressor_OLS = sm.OLS(endog = y, exog = X_opt).fit()

In [225]:
regressor_OLS.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                      y   R-squared:                       0.019
Model:                            OLS   Adj. R-squared:                  0.019
Method:                 Least Squares   F-statistic:                     232.6
Date:                Thu, 26 Mar 2020   Prob (F-statistic):               0.00
Time:                        17:29:47   Log-Likelihood:            -1.1490e+06
No. Observations:               82288   AIC:                         2.298e+06
Df Residuals:                   82280   BIC:                         2.298e+06
Df Model:                           7                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const       5.624e+06   1.82e+06      3.091      0.002    2.06e+06    9.19e+06
x1         -1.335e+05   9389.258    -14.223      0.000   -1.52e+05   -1.15e+05
x2         -1.879e+04   6263.087     -3.000      0.003   -3.11e+04   -6514.360
x3         -1.131e+05   4508.427    -25.092      0.000   -1.22e+05   -1.04e+05
x4         -3101.6953    913.259     -3.396      0.001   -4891.677   -1311.714
x5           286.9495     33.316      8.613      0.000     221.651     352.248
x6          4.936e-07   1.21e-07      4.063      0.000    2.55e-07    7.32e-07
x7         -5.243e-07   1.31e-07     -3.987      0.000   -7.82e-07   -2.67e-07
==============================================================================
Omnibus:                    92773.142   Durbin-Watson:                   1.971
Prob(Omnibus):                  0.000   Jarque-Bera (JB):          8793760.786
Skew:                           5.925   Prob(JB):                         0.00
Kurtosis:                      52.238   Cond. No.                     4.74e+14
==============================================================================

Warnings:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
[2] The condition number is large, 4.74e+14. This might indicate that there are
strong multicollinearity or other numerical problems.
"""

## Multiple Linear Regression Part II

In [205]:
# Splitting the dataset into the Training set and Test set
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.2, random_state = 0)

In [206]:
# Fitting Multiple Linear Regression to the Training set
from sklearn.linear_model import LinearRegression
regressor = LinearRegression()
regressor.fit(X_train, y_train)

LinearRegression(copy_X=True, fit_intercept=True, n_jobs=None,
         normalize=False)

In [207]:
# Predicting the Test set results
y_pred = regressor.predict(X_test)

In [208]:
print(y_pred)

[133469.94479625  95346.25066625 126442.88145854 ... 136585.50451872
  39526.06193607 103863.58852079]


In [209]:
print(y_test)

[523   0   0 ...   0  22   0]


In [213]:
print(y_pred.shape)

(16458,)


In [214]:
print(y_test.shape)

(16458,)


In [219]:
for y in y_test:
    print(y)

523
0
0
0
93761
0
4177
312
175214
35
7709
139
0
0
0
0
0
732
78220
836177
0
0
156
0
99038
171
2113
17023
1354207
261588
665
44
0
670439
0
0
1
6583
0
42
0
257049
0
698013
11055
0
0
4038
2375
0
203
7
0
44732
19
0
2928
0
37
0
5488
117579
4911
3192
0
893
8
758
133
0
368
64
0
568
0
54
0
9866
776
146
28
689913
0
51331
24015
487
0
916
0
0
598
53726
844
0
4582
183
25461
6992
0
409
4076
3507
93542
106558
253
0
0
64
140
0
65
3
348
266
1355
11091
0
729
26982
82
22
32743
0
34844
15883
0
6755
22934
0
0
42570
0
18090
46103
0
275987
21655
0
3765
3683
38
0
151
0
945478
3133
0
0
0
55564
2520
8026
40
1761
167665
47905
28
19190
2924
1551
265
27502
696
0
167936
31
0
0
0
597624
0
2599
4617
351954
260755
697889
0
166202
0
0
87
21035
2351
37625
1198
0
0
22435
49681
0
257711
608087
0
398097
11678
1686
0
16010
669
0
0
160883
2951
321
1027
0
292
23848
666
1218
296
30797
0
2226
2599
481143
8838
0
3031
1082
1252178
0
2488
0
246335
3404
46732
1274
69760
78197
0
268137
203791
32371
0
120235
54430
25584
34943
406700


2218
869
89989
548
51798
259921
170009
471325
0
76169
2578
36
0
942
702
41
0
1410
46571
48
0
160
5
0
46
795824
347
0
15723
0
0
2236
89
72
0
271644
587499
42197
0
59510
0
56
0
0
116
919
25818
0
0
29
1577
0
0
1643
0
30837
2538
0
2643
0
0
3075120
3499
0
153
33886
0
22843
0
966695
2
0
98
70
7649
16
2016
0
186
1362826
0
0
327
2118
92964
149
1181280
26170
0
0
64573
1182
0
144
1326
8560
0
308963
11072
0
2177
23396
2788
71371
0
0
21582
0
34008
46080
660
4523
0
0
74018
0
0
211118
204
0
0
0
0
34
6896
9079
0
21612
272766
791004
54963
140935
1663
287038
37112
566
1386
11758
699027
3096
0
0
0
454
367128
66
697
62
974
200
0
252234
1668
1018
3853
274221
0
150199
73864
64163
204274
0
30371
40342
0
21
0
48
338
375850
5702
0
756804
7079
0
111
50823
0
2284
682557
734974
2639
186864
0
1092107
2120
0
0
0
1169
11160
1290
171187
0
0
0
57264
0
0
64471
0
41
0
2791
2609
182
15614
13604
1611
42
1189769
518910
1395
0
27493
0
39157
62887
35
25141
3336
0
0
60329
0
682848
1869
59745
29385
14349
214714
0
0
202063
143

0
128
50
15068
325
0
611791
2
441
1065859
0
6031
28
538
129450
258648
0
0
274
17727
163
156
163783
8113
1279
2840
293252
35789
620
0
1480
416
0
0
170431
0
14820
21
267
2252
1944
3699
335
16059
4795
571237
4255
0
21372
3748
3692
0
58165
26
23153
0
127052
3086332
110
4628
230251
0
186240
85166
2476
7
0
527798
1155
0
78
23
23
78616
19
4604
0
0
2735
6685
80738
0
0
0
393952
24902
25420
0
389707
0
6047
0
41208
19838
525602
0
0
10811
395
0
3125
2013
0
0
0
2337
152
0
78
12
48
0
0
85035
1523
1857
2862
7787
57
0
256437
58598
6318
112729
18432
6333
3705
29922
0
0
0
0
2001
1165
0
293050
21967
9755
11394
0
306
2003102
25386
33474
723
0
637034
0
0
755
125231
223910
282
0
0
29495
130
132292
2169
626321
5444
0
0
0
70
1188
119933
148206
22178
40
0
150901
169699
0
25379
2328
0
695268
250224
0
1
797601
2830
834747
3344
107358
5085
251462
212386
52756
846742
17285
1762
20639
1831341
73829
3355
104601
21
208
0
169421
265
290447
40376
0
0
6963
71421
0
3913
205
1080
2822
3384
0
532468
1946
142114
0
294
115
0

0
0
0
0
1047
0
2869
0
0
411027
57942
0
0
1183
2534
821237
61693
0
190
0
91
15
119755
245402
25642
1162
87
177
27
365418
4385
0
2212
281170
1225
6176
0
1777
272450
221
28291
24
0
0
24
514
81871
17170
0
187
49308
11536
28330
511
0
151559
964676
14
0
77361
40241
91518
16923
3223
0
919
1245
305
442
3184
2651
20
54444
0
7505
0
0
0
351
598
127823
0
10593
156459
0
310
0
50
2416
418004
15381
21147
2120
11259
6372
1504
4019
213
211613
0
211
5133
466712
141092
3609336
49007
22337
245
0
0
564740
0
4196
58786
35193
6837
0
1008
76218
21839
535146
0
180391
3212
394672
0
0
81843
18300
151
4979
68377
274657
0
0
47322
3058
499
26365
84105
11506
1298
0
0
0
334
352
0
221
11619
0
1486697
88174
0
17631
423667
6331
0
51345
186
403800
125
2066
759576
67587
0
20641
0
0
193251
193
228
7115
725
33
18
0
0
53187
1729472
23672
0
242725
3622759
0
0
0
599
0
0
1479
0
726230
10177
0
0
374
508872
12189
1390
21586
4896
618571
0
15402
0
426507
687
1660
3032
0
357
0
32
17348
0
53
5
386
1597
149354
335
0
0
3432
54748
83578

2
9407
5303
0
15131
0
0
1765548
0
0
25860
6289
0
551228
2065547
903
0
54800
106761
47070
0
9
322
112
18
0
24
0
47
0
74
0
0
242055
350
175907
0
13
0
0
93
137680
31
0
116309
4412
1042
56340
21
290411
0
9
0
0
331
15734
3519
22000
0
41144
0
0
675209
0
119227
54815
26255
324
1928
54594
13750
33056
0
35
54
837
166
276
0
48
282
0
0
25036
79
1776
0
6438
1169514
2186
1945
0
209
9103
6425
1436832
7541
3250
559299
0
0
4916
431551
119011
3
46
21413
44
0
108
8827
46556
0
270
1427
269937
110598
329362
0
30
25707
167917
5930
395
1
2939
82
0
131385
56122
558983
0
5304
179
10043
361
194
5513
308504
0
23740
0
0
1
171667
7874
36858
3984
0
547481
0
81
405
161470
560
235581
713446
4064
0
120
443171
581869
608603
0
9447
676
706
4
21774
130
3367
0
0
0
901929
0
0
0
0
2463
302
0
28
0
459014
1471
10610
152672
321549
219
1204
440
0
27764
3254
56
4887
0
28883
575
38
0
3268
568
83000
634
4
89
0
25552
32
0
2506
0
0
0
9760
0
8239
1850
0
1701
13
0
61302
0
29127
47271
727
273
45335
41630
0
73050
140
1250211
0
276651
0

1411
1488465
8845
337
28020
330
501072
11993
0
531
0
3531
109528
2437
59526
0
26737
0
0
0
44
59686
0
2843
0
0
46904
4606
0
0
5437
0
579
22521
113
185864
145
296622
12206
11277
486582
108608
94
22940
0
0
3956
0
6161
0
21
160
691
3925
0
49027
315
630
0
9000
0
10837
32
0
8
2001
0
655
24
761
11377
0
0
16
0
0
57504
0
59269
0
2729
24272
22043
54
0
120
0
2378
6520
10144
1513
0
7753
233073
0
0
308
255975
175842
26117
0
2003746
50091
131
0
1722932
1878
526
4744
471
2588
436637
106045
821399
230
41537
1221841
0
0
0
217293
35334
0
2275
541
0
1412
1828
23281
0
0
4029
110
7629
0
0
0
864
594
2
0
8927
41644
0
997
2697
77
260896
1065
0
287
0
13151
91
475
200049
570943
40759
0
22
213
5671
342
1
1
314
64209
13960
0
3907
10203
404658
4659
3359
1701
0
224998
2199
0
60
0
2341
992387
418
0
1322585
0
128137
0
121
0
694607
0
58640
66553
1561
0
298753
0
5987
109
36157
184
122
639049
15
2268
0
90569
1078
23999
22
25595
4512
0
434
188
0
45
3834
42535
0
27
0
0
50610
601
0
3310
17
1431
0
2154
37
0
7687
0
3214
0
32

184
0
4022
69339
126034
84
435288
21805
0
0
0
0
2198
0
0
2274
164702
9620
2288
196687
25679
8
0
34
20
3208
55
3168
1491
33241
54902
370
71999
29191
115342
112
51941
33782
7855
0
255
120614
513
6099
0
0
0
76
0
51
57883
24258
0
0
0
17513
4496
4633
79502
225
0
0
6462
630244
48295
1364
0
7012
2849
181625
1674
56604
0
37
0
2721
5760
6941
4874
79127
0
0
0
2651
47459
48841
0
11843
0
431
1079
190
17828
0
0
870
288660
66383
0
3507
0
0
891667
768
0
1340
0
0
0
2513
7318
0
2
31225
0
0
0
632785
0
405
37226
40480
0
150381
46740
92134
41855
113938
9733
137
396267
1184
261
5331
31
0
165599
42600
69623
0
44642
401506
67571
58
55085
57111
0
0
350
5481
467
23947
8311
0
25439
0
41983
2658
0
12
561
12992
0
2385047
4691
122
0
85
0
21
96174
0
58499
359088
104068
63846
26081
0
0
116638
778618
150427
499
247
19498
0
0
133319
6536
0
0
0
21
50934
137977
96982
48037
11
0
6633
0
9558
5
393591
8797
5733
2767
0
0
1235903
0
349
10384
7322
349
3781
42
0
0
0
0
0
6957
23
33
34348
2540
5119
237082
504787
75464
0
6925
405

114854
0
0
0
202
63197
855
60123
793
142290
2138
107
210
327
22841
396
176531
66
848
29624
152436
508
58
5518
4
0
118700
840004
31
424
155
27940
46
233425
4309
0
21862
0
531894
2142
227414
0
131
835
359
0
1269
1452
0
0
3134
1645
137
212
0
42
0
0
57215
9079
211
43934
14
209438
15
4533
3767
877426
72769
1907
552831
0
1244216
0
102752
4204
0
3628
0
546463
196912
50117
115012
0
403896
87
100813
0
21518
169996
2510
17
0
0
573
10
17511
0
0
645
0
6117
586
0
907
0
317371
0
0
113532
35068
23405
657447
1497
10999
0
2086
960
320913
7085
24005
0
197041
28412
0
20777
55
0
34385
0
391
130851
0
0
165
545915
369
0
8
4723
1240311
192
15302
0
0
2268
0
210720
0
26971
0
2828
132
748312
1832
0
2188
7913
19
25474
4088
0
580360
353
496
168644
0
2892
3287
2033
44447
26131
0
7368
0
0
2192
0
34014
9857
6
8320
1954
0
33
0
147182
0
439
694573
23
118
133374
1314132
1360
3818
32
87762
480
0
0
10868
0
500
2233
0
0
41
0
96169
6
588
98
3652
990
0
27
0
1320
44382
273
656
171319
464
0
0
183
2943
26
73824
33624
0
34601
1

In [220]:
for y in y_pred:
    print(y)

133469.94479624648
95346.25066624675
126442.88145853672
130138.1167120738
13733.933930708095
100639.02766817529
127521.97299878579
86161.76931019966
97901.86453078687
54792.662306405604
98210.8355864659
138814.4936117651
116031.17515843548
84727.80796355568
86987.89592460915
97414.45017709583
136922.37257726863
117022.32527292147
10419.051313896663
86743.16181637812
86470.74036587868
138277.47935584933
45966.35339618754
136894.47557440028
100639.02766817529
12497.74086077325
139822.33463424444
124713.52387749683
131594.52346692514
96189.05599040724
101391.82007535361
126147.48522414081
42008.38775078952
126442.88145853672
129249.26779527962
99243.73659950309
135426.0854695579
89607.66226518247
38313.15249725245
55664.71040371712
50456.72145024408
84516.12747917697
38622.12355293147
84207.15642349795
136164.2818683209
125316.44306711014
50023.24617539905
36833.132903222926
141377.53598929476
123786.61071045976
85852.79825452063
98043.1911716992
135237.36870128382
47107.63973999955
13052

50993.735706159845
120504.76783308387
84418.83690787666
125580.80397586524
42626.32986214757
46678.414396915585
84418.83690787666
99712.11450113822
125889.77503154427
99897.01750577334
123786.61071045976
48343.52396271564
14192.388505680487
140374.1627572868
39858.007775647566
124404.55282181781
125271.83292018622
47725.581851357594
53865.749139368534
97883.70363531448
46987.38545259461
99380.52810589131
138611.5104020862
101315.36001038272
128595.98688900843
43553.24302918464
17700.504945719615
138487.36166061368
99836.61872030329
42008.38775078952
41772.620273518376
136894.47557440028
127830.94405446481
132906.86775461212
97294.19588969089
3383.792526319623
123477.63965478074
95440.36955561675
135992.6412334675
96908.75966045912
117885.00149250962
137849.2857443057
50000.6308358321
50955.44100573659
85507.27759366203
131594.52346692514
109.57966688461602
123786.61071045976
9801.109202538617
36990.05654319096
129373.33584632259
99897.01750577334
11440.083370303735
51284.545866366476
1

138196.55150040705
128904.95794468746
140992.10486864485
85816.24864934105
131594.52346692514
84727.80796355568
85507.27759366203
53247.80702801049
137684.59723504912
51259.13039811514
42317.35880646855
38069.01712593902
134087.88690760452
38069.01712593902
99408.42510875966
91152.51754357759
103169.18634445686
136613.4015215896
49430.719532292336
138505.52255608607
94419.33749920968
128114.83628403861
125007.47201143112
13901.578345473856
139079.88830372132
50048.66164365038
97217.73071613815
15527.36147931125
52001.57672863919
36372.11443183292
3383.792526319623
51408.69460783899
137821.38874143735
103245.64640942775
100205.98856145237
100454.56083166134
86678.92486893013
99836.61872030329
96985.22483401187
120504.76783308387
115874.25151846651
143176.49725364428
141377.53598929476
130138.1167120738
86060.98275757208
50337.49889437854
141377.53598929476
137537.4965118626
104117.6945067402
125719.5330121601
94822.4274442587
128760.67539826594
123786.61071045976
133215.83881029114
8497

43553.24302918464
137512.41768575832
126766.70046660211
125889.77503154427
141301.07592432387
126133.9104028577
141686.50704497378
50023.24617539905
134808.14335819986
125271.83292018622
134405.05341315083
115624.91353145614
85036.7790192347
138337.87814131938
115722.20410275646
137512.41768575832
138895.42146720737
97858.28816706408
96908.75966045912
138611.5104020862
98787.66482063755
100170.64976654015
133215.83881029114
42699.533440555446
126147.48522414081
84727.80796355568
126337.47512351815
127521.97299878579
133778.9158519255
141686.50704497378
138646.8491969984
86125.21970502008
18572.553043032065
49430.719532292336
53171.3469630396
126133.9104028577
130756.05882343184
135546.33975696284
85904.05911760312
136942.50638221856
36524.1618475439
84109.86585219763
50000.6308358321
89607.66226518247
13733.933930708095
50332.21723107807
1815.962464028038
3383.792526319623
49448.88042776473
117663.24216817506
137869.41954925563
135237.36870128382
12908.473475146107
117058.87487810012
1

97698.88132110797
98787.66482063755
97698.88132110797
48480.85438354127
97265.76152395643
42626.32986214757
16697.131713711657
84668.17489488702
50993.735706159845
100046.50102506764
134087.88690760452
127678.76568125281
98828.77769782394
14519.520456831902
95131.39849993773
88015.5956442738
1594.8018766110763
103245.64640942775
50023.24617539905
125271.83292018622
127060.82356989477
126133.9104028577
96936.65666332748
98453.61493885424
91152.51754357759
100046.50102506764
49719.5567830205
95571.1138790492
138302.53934640717
101006.3889547037
131374.0009347899
127369.79462557379
125316.44306711014
102881.8102840241
103169.18634445686
126777.19050262962
39526.061936072074
85654.72113059275
14519.520456831902
51444.0334027512
16697.131713711657
99119.58785803057
98785.20133410115
102627.7042980697
138277.47935584933
56282.65251507517
54737.79723668005
100046.50102506764
129806.81112116762
134190.2012468418
85904.05911760312
116031.17515843548
87693.04976731166
138178.39060493466
138487.3

...

117058.87487810012
137375.6261793701
98600.7344975872
49101.61467166245
96273.16383328382
49281.23601299804
101315.36001038272
143176.49725364428
139079.88830372132
98476.23027842212
135546.33975696284
86434.1907606991
97526.70177181717
128471.83814753685
97425.24906034116
126337.47512351815
133469.94479624648
53247.80702801049
49714.27511972003
129249.26779527962
94822.4274442587
38290.17771335598
126751.85251421575
137578.609389049
134714.02446882986
17700.504945719615
99897.01750577334
84418.83690787666
100697.41789902467
53556.77808368951
138586.45041152835
96985.22483401187
109.57966688461602
86766.13660027459
46893.266563224606
120813.73888876289
99096.63587631658
98007.85237678699
128423.80733971763
99096.63587631658
97245.6277190065
55410.60441776365
141686.50704497378
35656.88174917456
50048.66164365038
128780.80920321587
85816.24864934105
99071.55705021229
125580.80397586524
96315.89637520537
137269.63833336998
126728.87773031928
95571.1138790492
49589.89822145924
97723.42123

15527.36147931125
130211.32029048167
124192.8723374391
134808.14335819986
36681.08548751194
125719.5330121601
48045.04294306412
48480.85438354127
137101.9939186033
125022.49493317585
137251.47743789759
131065.02987911087
136613.4015215896
92933.14029924385
46275.32445186656
36583.79491621163
127521.97299878579
137101.9939186033
142613.42021201085
130520.2913461607
142867.52619796526
137993.56829072814
515.8412938639522
128780.80920321587
126110.93561896123
87075.10765595362
48455.77555743698
121358.47742171306
127805.86522835959
127830.94405446481
135855.31081264187
137869.41954925563
99071.55705021229
98785.20133410115
49739.69058797136
51259.13039811514
99527.64766462427
38290.17771335598
138611.5104020862
126419.90667464025
96624.86743088439
42081.5913291974
49719.5567830205
42317.35880646855
37708.78520717658
85654.72113059275
96599.7886047801
98625.79448814504
126457.72941092309
121122.70994444191
97901.86453078687
138770.9172480423
134808.14335819986
137849.2857443057
126337.4751

49590.20706867706
129107.94115436636
96367.28272265382
141377.53598929476
88288.01709477324
124911.60100142471
84825.09853485599
13574.44639432244
133778.9158519255
95571.1138790492
142867.52619796526
52619.51883999724
37451.07501458097
15527.36147931125
86457.16554459557
138814.4936117651
37399.81415149756
136585.50451872125
85852.79825452063
45657.38234050851
128451.70434258692
91770.45965493564
129249.26779527962
130115.78217684664
138302.53934640717
93801.39538785163
37451.07501458097
116749.9038224211
141940.6130309282
38313.15249725245
126148.75835524406
39858.007775647566
88310.99187866971
88310.99187866971
16697.131713711657
51259.13039811514
95131.39849993773
100639.02766817529
86161.76931019966
137203.4466300793
46893.266563224606
134405.05341315083
124911.60100142471
38931.094608610496
90225.60437654052
48792.64361598343
50334.68071761541
137821.38874143735
39526.061936072074
137228.5254561836
47914.29861963168
137887.58044472802
124344.91975314915
126457.72941092309
141301.

141301.07592432387
94942.68173166364
98909.70555326622
116440.93276674207
138487.36166061368
85036.7790192347
137410.9649742823
103863.5885207858
3383.792526319623
96315.89637520537
38069.01712593902
136610.58334482554
94419.33749920968
138814.4936117651
100373.63297621906
134808.14335819986
137887.58044472802
134714.02446882986
46987.38545259461
16697.131713711657
88310.99187866971
128423.80733971763
13863.283645051531
49589.89822145924
97265.76152395643
85234.85614316259
96315.89637520537
127086.16155830864
50334.68071761541
51611.67781751789
93492.42433217261
85595.08806192409
55410.60441776365
14166.973037430085
37399.81415149756
48354.01399874315
121976.41953307111
127086.16155830864
11869.30871338863
36990.05654319096
127060.82356989477
94822.4274442587
135426.0854695579
124810.81444879714
46678.414396915585
94822.4274442587
129416.91221004538
90770.34290949069
53789.289074397646
105044.60767377727
95251.65278734267
42935.30091782659
142558.55514228623
53171.3469630396
124404.552

125719.5330121601
98909.70555326622
49121.74847661331
47107.63973999955
138586.45041152835
109.57966688461602
125801.9645632822
87693.04976731166
47914.29861963168
101315.36001038272
125316.44306711014
99119.58785803057
1594.8018766110763
137849.2857443057
15527.36147931125
42008.38775078952
123883.90128176007
49121.74847661331
46678.414396915585
128595.98688900843
132212.46557828318
49716.738606257364
126028.50406783912
93801.39538785163
136164.2818683209
95251.65278734267
84418.83690787666
134190.2012468418
99218.67660894524
95869.59489870071
49863.83932944387
86522.00122896116
124653.89080882818
115874.25151846651
116492.19362982456
141940.6130309282
37399.81415149756
46678.414396915585
138277.47935584933
136585.50451872125
39526.061936072074
103863.5885207858


In [227]:
from scipy import stats
stats.describe(y_pred)

DescribeResult(nobs=16458, minmax=(109.57966688461602, 159965.54319163226), mean=90363.09147866121, variance=1608002941.8278708, skewness=-0.527972711871747, kurtosis=-0.8791483355137353)